In [4]:
# from tqdm import tqdm
from tqdm.notebook import tqdm
from datasets import load_dataset, DatasetDict, load_from_disk
# from transformers import GPT2Tokenizer, GPT2Config, GPT2LMHeadModel, GPT2LMHeadModel
# from transformers import DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments
import accelerate
import transformers
# transformers.__version__, accelerate.__version__
import torch
# torch.cuda.is_available()
# from scripts.utils import *
from pathlib import Path

import sys
import os

scripts_dir = os.path.abspath(os.path.join(os.getcwd(), '..', 'scripts'))

if scripts_dir not in sys.path:
    sys.path.append(scripts_dir)

from utils import *
from candor_surprisals import main, concat_surprisals_to_full_df
from candor_final_df import make_df_from_convo_path, make_big_df_from_all_convo_paths, choose_and_convert_text_df_to_list_based_on_context_size_and_direction, prepare_candor_text_dfs

# device = "cuda" if torch.cuda.is_available() else "cpu"
# print(torch.cuda.get_device_name(0))


In [6]:
# candor_full_df_path = '../data/candor/sample/0020a0c5-1658-4747-99c1-2839e736b481/'
candor_outer_path = '../data/candor/sample/0020a0c5-1658-4747-99c1-2839e736b481/'

models = {
    ('left', 'sentence'): '../models/gpt2/left_sentence/checkpoint-76066',
    ('right', 'sentence'): '../models/gpt2/right_sentence/checkpoint-76066',
    ('bidi', 'sentence'): '../models/gpt2/bidi_sentence/checkpoint-76066',
    ('left', 'bigram'): '../models/gpt2/left_bigram/checkpoint-63819',
    ('right', 'bigram'): '../models/gpt2/right_bigram/checkpoint-63819',
    ('bidi', 'bigram'): '../models/gpt2/bidi_bigram/checkpoint-100000',
}


In [ ]:
big_df = make_big_df_from_all_convo_paths(candor_outer_path, out_path=Path('../data/candor/'))

In [ ]:
big_df = big_df[big_df.columns[[0, 11, 12, 13, *range(1, 11)]]]
big_df['duration'] = big_df['word_stop'] - big_df['word_start']
big_df['ends_with_punct'] = big_df['word'].apply(lambda x: any(x.endswith(punc) for punc in {'.', ',', '?', '!'}))
big_df

In [ ]:
text_sentence, text_bigram, text_trigram = prepare_candor_text_dfs(big_df)

In [5]:
all_model_surprisals = {}
for (context_direction, context_size), model_dir in models.items():
    texts = choose_and_convert_text_df_to_list_based_on_context_size_and_direction(text_sentence, text_bigram, text_trigram, context_size, context_direction)
    model_surprisals = main(texts, model_dir, context_size, context_direction)
    all_model_surprisals[(context_direction, context_size)] = model_surprisals

Loading pretrained model from ../models/gpt2/left_sentence/checkpoint-76066...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['[BOS]', '[EOS]', '<|endoftext|>']
...done



100%|██████████| 856/856 [00:06<00:00, 124.03it/s]


Loading pretrained model from ../models/gpt2/right_sentence/checkpoint-76066...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['[BOS]', '[EOS]', '<|endoftext|>']
...done



100%|██████████| 856/856 [00:06<00:00, 125.60it/s]


Loading pretrained model from ../models/gpt2/bidi_sentence/checkpoint-76066...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['[BOS]', '[EOS]', '<|endoftext|>', '[SEP]', '[FILLER]', '[BLANK]']
...done



...

100%|██████████| 7721/7721 [00:39<00:00, 197.12it/s]


Loading pretrained model from ../models/gpt2/right_bigram/checkpoint-63819...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['<s>', '</s>', '<|endoftext|>']
...done



100%|██████████| 7721/7721 [00:40<00:00, 191.84it/s]


Loading pretrained model from ../models/gpt2/bidi_bigram/checkpoint-100000...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['<s>', '</s>', '<|endoftext|>', '[SEP]', '[FILLER]', '[BLANK]']
...done



100%|██████████| 7721/7721 [00:52<00:00, 146.87it/s]


In [7]:
full_df = make_df_from_convo_path(Path(candor_convo_path))

In [8]:
full_df

turn_id    word word_start word_stop   text  lemma n_chars n_syllables  \
0           0    Mhm.       4.34      4.66    Mhm    Mhm       3           2   
1           0    Mhm.      10.14     10.95    Mhm    Mhm       3           2   
2           0   Just,      12.74     14.36   Just   just       4           1   
3           0     mm.      17.74     17.95     mm     mm       2        None   
4           0     And      18.74     19.06    And    and       3           1   
...       ...     ...        ...       ...    ...    ...     ...         ...   
7716      322    good    2732.43   2732.56   good   good       4           1   
7717      322  night.    2732.56    2733.0  night  night       5           1   
7718      323   Yeah.    2732.59   2732.79   Yeah   yeah       4           1   
7719      323   Yeah.    2733.29   2734.09   Yeah   yeah       4           1   
7720      324     But    2734.39   2734.66    But    but       3           1   

        pos stopword    mtw sentence_id_in_turn word_id_in_sentence  \
0     PROPN    False  False                   0                   0   
1     PROPN    False  False                   1                   0   
2       ADV     True  False                   2                   0   
3      INTJ    False  False                   2                   1   
4     CCONJ     True  False                   3                   0   
...     ...      ...    ...                 ...                 ...   
7716    ADJ    False  False                   1                   2   
7717   NOUN    False  False                   1                   3   
7718   INTJ    False  False                   0                   0   
7719   INTJ    False  False                   1                   0   
7720  CCONJ     True  False                   0                   0   

      position_in_turn  
0                    0  
1                    1  
2                    2  
3                    3  
4                    4  
...                ...  
7716                 5  
7717                 6  
7718                 0  
7719                 1  
7720                 0  

[7721 rows x 14 columns]

In [10]:
full_df = full_df[full_df.columns[[0, 11, 12, 13, *range(1, 11)]]]
full_df['duration'] = full_df['word_stop'] - full_df['word_start']
full_df['ends_with_punct'] = full_df['word'].apply(lambda x: any(x.endswith(punc) for punc in {'.', ',', '?', '!'}))
full_df

turn_id    pos stopword    mtw sentence_id_in_turn word_id_in_sentence  \
0           0  PROPN    False  False                   0                   0   
1           0  PROPN    False  False                   1                   0   
2           0    ADV     True  False                   2                   0   
3           0   INTJ    False  False                   2                   1   
4           0  CCONJ     True  False                   3                   0   
...       ...    ...      ...    ...                 ...                 ...   
7716      322    ADJ    False  False                   1                   2   
7717      322   NOUN    False  False                   1                   3   
7718      323   INTJ    False  False                   0                   0   
7719      323   INTJ    False  False                   1                   0   
7720      324  CCONJ     True  False                   0                   0   

      position_in_turn    word word_start word_stop   text  lemma n_chars  \
0                    0    Mhm.       4.34      4.66    Mhm    Mhm       3   
1                    1    Mhm.      10.14     10.95    Mhm    Mhm       3   
2                    2   Just,      12.74     14.36   Just   just       4   
3                    3     mm.      17.74     17.95     mm     mm       2   
4                    4     And      18.74     19.06    And    and       3   
...                ...     ...        ...       ...    ...    ...     ...   
7716                 5    good    2732.43   2732.56   good   good       4   
7717                 6  night.    2732.56    2733.0  night  night       5   
7718                 0   Yeah.    2732.59   2732.79   Yeah   yeah       4   
7719                 1   Yeah.    2733.29   2734.09   Yeah   yeah       4   
7720                 0     But    2734.39   2734.66    But    but       3   

     n_syllables duration  ends_with_punct  
0              2     0.32             True  
1              2     0.81             True  
2              1     1.62             True  
3           None     0.21             True  
4              1     0.32            False  
...          ...      ...              ...  
7716           1     0.13            False  
7717           1     0.44             True  
7718           1      0.2             True  
7719           1      0.8             True  
7720           1     0.27            False  

[7721 rows x 16 columns]

In [9]:
for k, v in all_model_surprisals.items():
    print(k, len(v))

('left', 'sentence') 7721
('right', 'sentence') 7721
('bidi', 'sentence') 7721
('left', 'bigram') 7721
('right', 'bigram') 7721
('bidi', 'bigram') 7721


In [10]:
out_df = concat_surprisals_to_full_df(full_df, {'_'.join(k): v for k, v in all_model_surprisals.items()})

In [11]:
out_df

turn_id sentence_id_in_turn word_id_in_sentence  position_in_turn  \
0           0                   0                   0                 0   
1           0                   1                   0                 1   
2           0                   2                   0                 2   
3           0                   2                   1                 3   
4           0                   3                   0                 4   
...       ...                 ...                 ...               ...   
7716      322                   1                   2                 5   
7717      322                   1                   3                 6   
7718      323                   0                   0                 0   
7719      323                   1                   0                 1   
7720      324                   0                   0                 0   

        word word_start word_stop   text  lemma n_chars  ...    pos stopword  \
0       Mhm.       4.34      4.66    Mhm    Mhm       3  ...  PROPN    False   
1       Mhm.      10.14     10.95    Mhm    Mhm       3  ...  PROPN    False   
2      Just,      12.74     14.36   Just   just       4  ...    ADV     True   
3        mm.      17.74     17.95     mm     mm       2  ...   INTJ    False   
4        And      18.74     19.06    And    and       3  ...  CCONJ     True   
...      ...        ...       ...    ...    ...     ...  ...    ...      ...   
7716    good    2732.43   2732.56   good   good       4  ...    ADJ    False   
7717  night.    2732.56    2733.0  night  night       5  ...   NOUN    False   
7718   Yeah.    2732.59   2732.79   Yeah   yeah       4  ...   INTJ    False   
7719   Yeah.    2733.29   2734.09   Yeah   yeah       4  ...   INTJ    False   
7720     But    2734.39   2734.66    But    but       3  ...  CCONJ     True   

        mtw duration left_sentence  right_sentence  bidi_sentence  \
0     False     0.32     14.247051       17.214086       6.310241   
1     False     0.81     14.247051       17.214086       6.310241   
2     False     1.62      9.744504       10.990050       6.055397   
3     False     0.21     12.407815       11.694961       6.108757   
4     False     0.32      2.748569       12.719169       9.426615   
...     ...      ...           ...             ...            ...   
7716  False     0.13      1.356899        3.564446       9.403681   
7717  False     0.44      2.878433        6.771707       5.927935   
7718  False      0.2      4.249014        3.994786       5.398063   
7719  False      0.8      4.249014        3.994786       5.398063   
7720  False     0.27      3.637504       13.285196      10.514117   

      left_bigram  right_bigram  bidi_bigram  
0       18.384441     18.408640    30.430573  
1       18.384441     18.408640    30.430573  
2        6.128322      9.310482    19.339494  
3       12.510981     12.028164    20.514782  
4        2.312116      8.054623     2.546889  
...           ...           ...          ...  
7716     4.064208      3.977333     6.232678  
7717     5.639752      6.654217    18.155780  
7718     5.594672      4.854791    18.202595  
7719     5.594672      4.854791    18.202595  
7720     3.167184     12.125416     4.100402  

[7721 rows x 21 columns]

In [12]:
import pandas as pd

In [13]:
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
#     display(out_df)

In [14]:
out_df.to_csv('../results/sample.csv')

In [13]:
out_df = pd.read_csv('../results/sample.csv')
out_df

Unnamed: 0  turn_id  sentence_id_in_turn  word_id_in_sentence  \
0              0        0                    0                    0   
1              1        0                    1                    0   
2              2        0                    2                    0   
3              3        0                    2                    1   
4              4        0                    3                    0   
...          ...      ...                  ...                  ...   
7716        7716      322                    1                    2   
7717        7717      322                    1                    3   
7718        7718      323                    0                    0   
7719        7719      323                    1                    0   
7720        7720      324                    0                    0   

      position_in_turn    word  word_start  word_stop   text  lemma  ...  \
0                    0    Mhm.        4.34       4.66    Mhm    Mhm  ...   
1                    1    Mhm.       10.14      10.95    Mhm    Mhm  ...   
2                    2   Just,       12.74      14.36   Just   just  ...   
3                    3     mm.       17.74      17.95     mm     mm  ...   
4                    4     And       18.74      19.06    And    and  ...   
...                ...     ...         ...        ...    ...    ...  ...   
7716                 5    good     2732.43    2732.56   good   good  ...   
7717                 6  night.     2732.56    2733.00  night  night  ...   
7718                 0   Yeah.     2732.59    2732.79   Yeah   yeah  ...   
7719                 1   Yeah.     2733.29    2734.09   Yeah   yeah  ...   
7720                 0     But     2734.39    2734.66    But    but  ...   

        pos  stopword    mtw  duration  left_sentence  right_sentence  \
0     PROPN     False  False      0.32      14.247051       17.214086   
1     PROPN     False  False      0.81      14.247051       17.214086   
2       ADV      True  False      1.62       9.744504       10.990050   
3      INTJ     False  False      0.21      12.407815       11.694961   
4     CCONJ      True  False      0.32       2.748569       12.719169   
...     ...       ...    ...       ...            ...             ...   
7716    ADJ     False  False      0.13       1.356899        3.564446   
7717   NOUN     False  False      0.44       2.878433        6.771707   
7718   INTJ     False  False      0.20       4.249014        3.994786   
7719   INTJ     False  False      0.80       4.249014        3.994786   
7720  CCONJ      True  False      0.27       3.637504       13.285196   

      bidi_sentence  left_bigram  right_bigram  bidi_bigram  
0          6.310241    18.384441     18.408640    30.430573  
1          6.310241    18.384441     18.408640    30.430573  
2          6.055397     6.128322      9.310482    19.339494  
3          6.108757    12.510981     12.028164    20.514782  
4          9.426615     2.312116      8.054623     2.546889  
...             ...          ...           ...          ...  
7716       9.403681     4.064208      3.977333     6.232678  
7717       5.927935     5.639752      6.654217    18.155780  
7718       5.398063     5.594672      4.854791    18.202595  
7719       5.398063     5.594672      4.854791    18.202595  
7720      10.514117     3.167184     12.125416     4.100402  

[7721 rows x 22 columns]

In [5]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    display(out_df)

Unnamed: 0  turn_id  sentence_id_in_turn  word_id_in_sentence  \
0              0        0                    0                    0   
1              1        0                    1                    0   
2              2        0                    2                    0   
3              3        0                    2                    1   
4              4        0                    3                    0   
5              5        0                    3                    1   
6              6        0                    3                    2   
7              7        0                    3                    3   
8              8        0                    4                    0   
9              9        0                    5                    0   
10            10        0                    6                    0   
11            11        0                    7                    0   
12            12        0                    8                    0   
13            13        0                    8                    1   
14            14        0                    9                    0   
15            15        0                   10                    0   
16            16        0                   11                    0   
17            17        0                   12                    0   
18            18        0                   13                    0   
19            19        0                   14                    0   
20            20        0                   15                    0   
21            21        0                   15                    1   
22            22        0                   16                    0   
23            23        0                   17                    0   
24            24        0                   18                    0   
25            25        0                   19                    0   
26            26        0                   20                    0   
27            27        0                   21                    0   
28            28        0                   22                    0   
29            29        0                   23                    0   
30            30        0                   24                    0   
31            31        0                   25                    0   
32            32        0                   26                    0   
33            33        0                   27                    0   
34            34        0                   28                    0   
35            35        0                   29                    0   
36            36        0                   30                    0   
37            37        0                   31                    0   
38            38        1                    0                    0   
39            39        1                    0                    1   
40            40        1                    0                    2   
41            41        1                    0                    3   
42            42        2                    0                    0   
43            43        2                    0                    1   
44            44        2                    0                    2   
45            45        2                    0                    3   
46            46        2                    0                    4   
47            47        3                    0                    0   
48            48        3                    1                    0   
49            49        3                    2                    0   
50            50        3                    2                    1   
51            51        3                    2                    2   
52            52        3                    2                    3   
53            53        3                    2                    4   
54            54        3                    2                    5   
55            55        3     